In [2]:
from hcloud import Client
client = Client(
    token="KccUEiddxtzGoLWSNC3V8tylq7MYHCjdnShtgasQ8jSbHqCjGoaa6Rq7yoz4uS23"
)
PREFIX = "s444498"
YOUR_LOCAL_SSH_PUBKEY = "ssh-ed25519 AAAAC3NzaC1lZDI1NTE5AAAAIAj15oTbXA0KGBw5V/76KXDgJZpLNrxUO/rTA0u0eRl1 wirus@wirusowylapek"
try:
    ssh_key = client.ssh_keys.create(name=f"{PREFIX}-pzc-ssh-key-2", public_key=YOUR_LOCAL_SSH_PUBKEY)
    print(f"Key {ssh_key.data_model.name} created: {ssh_key.data_model.public_key}")
except:
    ssh_key = client.ssh_keys.get_by_name(f"{PREFIX}-pzc-ssh-key-2")
    print(f"Key {ssh_key.data_model.name} already in use: {ssh_key.data_model.public_key}")

Key s444498-pzc-ssh-key-2 already in use: ssh-ed25519 AAAAC3NzaC1lZDI1NTE5AAAAIAj15oTbXA0KGBw5V/76KXDgJZpLNrxUO/rTA0u0eRl1 wirus@wirusowylapek


In [ ]:
from hcloud.networks.domain import NetworkSubnet

try:
    vnet = client.networks.create(
        name=f"{PREFIX}-pzc-test-vnet", 
        ip_range="10.10.10.0/24", 
        subnets=[
            NetworkSubnet(ip_range="10.10.10.0/24", network_zone="eu-central", type="cloud")
        ]
    )
    print(f"Created network: {vnet.data_model.name} ({vnet.data_model.ip_range})")
except:
    vnet = client.networks.get_by_name(
        f"{PREFIX}-pzc-test-vnet", 
    )
    print(f"Network in use: {vnet.data_model.name} ({vnet.data_model.ip_range})")

In [ ]:
from hcloud.locations.domain import Location
from hcloud.images.domain import Image
from hcloud.server_types.domain import ServerType

cloud_init_mysql=r'''#cloud-config
packages:
  - apt-transport-https
  - ca-certificates
  - curl
  - gnupg-agent
  - software-properties-common

write_files:
  - path: /root/docker-compose.yml
    content: |
        version: '3.9'

        services:
          db:
            image: mysql:5.7
            restart: always
            environment:
              MYSQL_DATABASE: gitea
              MYSQL_USER: gitea
              MYSQL_PASSWORD: gitea
              MYSQL_ROOT_PASSWORD: gitea
            ports:
              - "10.10.10.2:3306:3306"
            volumes:
              - my-db:/var/lib/mysql
          phpmyadmin:
            image: phpmyadmin
            restart: always
            ports:
              - "8080:80"
        volumes:
          my-db: {}

runcmd:
  - curl -fsSL https://download.docker.com/linux/ubuntu/gpg | apt-key add -
  - add-apt-repository "deb [arch=amd64] https://download.docker.com/linux/ubuntu $(lsb_release -cs) stable"
  - apt-get update -y
  - apt-get install -y docker-ce docker-ce-cli containerd.io
  - curl -L "https://github.com/docker/compose/releases/download/1.29.2/docker-compose-$(uname -s)-$(uname -m)" -o /usr/local/bin/docker-compose
  - chmod +x /usr/local/bin/docker-compose
  - systemctl start docker
  - systemctl enable docker
  - cd /root/ && docker-compose up -d
  '''

for i in range(20):

  mysql_server = client.servers.create(
      name=f"{PREFIX}-mysql-{i}", 
      server_type=ServerType("cx11"), 
      image=Image(name="ubuntu-20.04"), 
      ssh_keys=[ssh_key], 
      networks=[vnet], 
      location=Location("hel1"), 
      user_data=cloud_init_mysql
  )

  mysql_server.action.wait_until_finished()
  print(f"Creating gitea server: {mysql_server.action.complete}")

NameError: name 'client' is not defined

In [8]:
servers = client.servers.get_all()
print(f"Usuwanie {len(servers)} serwerów")
for s in servers:
    if s.data_model.name.startswith(PREFIX):
        action = client.servers.delete(s)
        print(f"\tUsuwanie serwera {s.data_model.name} ({s.data_model.public_net.ipv4.ip}): {action.data_model.status}")

Usuwanie 9 serwerów
